In [6]:
# Import libraries
import pandas as pd
import numpy as np
import math

import geopandas 
import json

from bokeh.io import output_notebook, show, output_file
from bokeh.plotting import figure
from bokeh.models import GeoJSONDataSource, LinearColorMapper, ColorBar, NumeralTickFormatter
from bokeh.palettes import brewer

from bokeh.io.doc import curdoc
from bokeh.models import Slider, HoverTool, Select
from bokeh.layouts import widgetbox, row, column


gdf = geopandas.read_file('pluto_subset_wgeometry/pluto_subset_wgeometry.shp')

# This dictionary contains the formatting for the data in the plots
format_data = [#('bbl', 0, 100,'0,0', 'BBL'),
               ('assesstot', 0, 10000000,'$0,0', 'Assessed Lot Total Value ($)'),
               ('unitsres', 0, 1000, '0,0', 'Number of Residential Units'),
               ('lotarea', 0 , 7000000,'0,0', 'Total Lot Area (sqft)'),
               #('landuse', 0, 2000,'0,0', 'Land Use Type Code'),
               ('numbldgs', 0, 10,'0,0', 'Number of Buildings')
              ]
 
#Create a DataFrame object from the dictionary 
format_df = pd.DataFrame(format_data, columns = ['field' , 'min_range', 'max_range' , 'format', 'verbage'])
#format_df.head(10)

# Create a function the returns json_data for the year selected by the user
def json_data(selectedValue):
    
    print('what is the selectedValue in json_data:', selectedValue)
    val = selectedValue
    
    # Pull lots with total values above from the dataset
    df_val = gdf[gdf['assesstot'] >= val]
    print('what is the size of the dataset: ', df_val.shape)
    
    print('what are the columns?', df_val.columns)
    # Merge the GeoDataframe object (sf) with the neighborhood summary data (neighborhood)
    #merged = pd.merge(sf, df_yr, on='subdist_no', how='left')
    
    # Fill the null values
    values = {'assesstot': 0, 'unitsres': 0, 'lotarea': 0, #'landuse': np.nan,
              'numbldgs': 0}

    df_val = df_val.fillna(value=values)
    
    # Bokeh uses geojson formatting, representing geographical features, with json
    # Convert to json
    df_val_json = json.loads(df_val.to_json())
    
    # Convert to json preferred string-like object 
    json_data = json.dumps(df_val_json)
    return json_data
  
# Define the callback function: update_plot
def update_plot(attr, old, new):
    # The input is the minimum assessed value selected from the slider
    print(slider.value)
    assess_value = slider.value
    new_data = json_data(assess_value)
    
    #print('what is new data?', new_data)
    #print('what are the updated data' new_data.columns)
    
    # The input cr is the criteria selected from the select box
    print('what is the new cr?', select.value)
    cr = select.value
    input_field = format_df.loc[format_df['verbage'] == cr, 'field'].iloc[0]
    print('what is the new input_field?', input_field)
    # Update the plot based on the changed inputs
    p = make_plot(input_field)
    
    # Update the layout, clear the old document and display the new document
    layout = column(p, widgetbox(select), widgetbox(slider))
    curdoc().clear()
    curdoc().add_root(layout)
    
    # Update the data
    geosource.geojson = new_data 
    
# Create a plotting function
def make_plot(field_name):    
  # Set the format of the colorbar
  min_range = format_df.loc[format_df['field'] == field_name, 'min_range'].iloc[0]
  max_range = format_df.loc[format_df['field'] == field_name, 'max_range'].iloc[0]
  field_format = format_df.loc[format_df['field'] == field_name, 'format'].iloc[0]

  # Instantiate LinearColorMapper that linearly maps numbers in a range, into a sequence of colors.
  color_mapper = LinearColorMapper(palette = palette, low = min_range, high = max_range)

  # Create color bar.
  format_tick = NumeralTickFormatter(format=field_format)
  color_bar = ColorBar(color_mapper=color_mapper, label_standoff=18, formatter=format_tick,
  border_line_color=None, location = (0, 0))

  # Create figure object.
  verbage = format_df.loc[format_df['field'] == field_name, 'verbage'].iloc[0]

  p = figure(title = verbage + ' Above the Selected Assessed Total Value', 
             plot_height = 650, plot_width = 850,
             toolbar_location = None)
  p.xgrid.grid_line_color = None
  p.ygrid.grid_line_color = None
  p.axis.visible = False

  # Add patch renderer to figure. 
  p.patches('xs','ys', source = geosource, fill_color = {'field' : field_name, 'transform' : color_mapper},
          line_color = 'black', line_width = 0.25, fill_alpha = 1)
  
  # Specify color bar layout.
  p.add_layout(color_bar, 'right')

  # Add the hover tool to the graph
  p.add_tools(hover)
  return p
    
    
# Input geojson source that contains features for plotting for:
# initial threshold is set at 50,000 USD 
geosource = GeoJSONDataSource(geojson = json_data(50000))
input_field = 'unitsres'

# Define a sequential multi-hue color palette.
palette = brewer['Blues'][8]

# Reverse color order so that dark blue is highest obesity.
palette = palette[::-1]

# Add hover tool

hover = HoverTool(tooltips = [ #('BBL','@bbl'),
                              ('Assessed total value in USD', '$@assesstot{,}'),
                              ('Number of Residential Units', '@unitsres'),
                              ('Total Lot Area (sqft)', '@lotarea'),
                              ('Number of Buildings', '@numbldgs')
                               ])
                               

# Call the plotting function
p = make_plot(input_field)

# Make a slider object: slider 
slider = Slider(title = 'Assessed Total Value Equal or Above',start = 0, end = 1000000, step = 50000, value = 50000, ) # what is the value doing here
slider.on_change('value', update_plot)

# Make a selection object: select
select = Select(title='Select Criteria:', value='Number of Residential Units', options=['Number of Residential Units', 'Total Lot Area (sqft)', 
              'Number of Buildings'])

select.on_change('value', update_plot)

# Make a column layout of widgetbox(slider) and plot, and add it to the current document
# Display the current document
layout = column(p, widgetbox(select), widgetbox(slider))
curdoc().add_root(layout)

# Use the following code to test in a notebook
# Interactive features will no show in notebook
output_notebook()
show(p)

Loading BokehJS ...